In [1]:
import logging
logger = logging.getLogger()
logger.setLevel(logging.DEBUG)
logging.debug('Needed to run for Jupyter Notebook')

DEBUG:root:Needed to run for Jupyter Notebook


In [2]:
import acme

In [3]:
environment_library = 'gym'

In [4]:
import IPython

from acme import environment_loop
from acme import specs
from acme import wrappers
from acme.agents.tf import d4pg
from acme.tf import networks
from acme.tf import utils as tf2_utils
from acme.utils import loggers
import numpy as np
import sonnet as snt

from absl import app
from absl import flags
import acme
from acme.agents.tf import dqn
from acme.tf import networks

# Import the selected environment lib
if environment_library == 'dm_control':
  from dm_control import suite
elif environment_library == 'gym':
  import gym

# Imports required for visualization
import pyvirtualdisplay
import imageio
import base64

# Set up a virtual display for rendering.
display = pyvirtualdisplay.Display(visible=0, size=(1400, 900)).start()

DEBUG:matplotlib:matplotlib data path: /home/hayato/anaconda3/envs/acme/lib/python3.8/site-packages/matplotlib/mpl-data
DEBUG:matplotlib:CONFIGDIR=/home/hayato/.config/matplotlib
DEBUG:matplotlib:matplotlib version 3.4.2
DEBUG:matplotlib:interactive is False
DEBUG:matplotlib:platform is linux
DEBUG:matplotlib:loaded modules: ['sys', 'builtins', '_frozen_importlib', '_imp', '_warnings', '_io', 'marshal', 'posix', '_frozen_importlib_external', '_thread', '_weakref', 'time', 'zipimport', '_codecs', 'codecs', 'encodings.aliases', 'encodings', 'encodings.utf_8', '_signal', '__main__', 'encodings.latin_1', '_abc', 'abc', 'io', '_stat', 'stat', '_collections_abc', 'genericpath', 'posixpath', 'os.path', 'os', '_sitebuiltins', '_locale', '_bootlocale', 'types', 'importlib._bootstrap', 'importlib._bootstrap_external', 'warnings', 'importlib', 'importlib.machinery', 'importlib.abc', '_operator', 'operator', 'keyword', '_heapq', 'heapq', 'itertools', 'reprlib', '_collections', 'collections', '_fun

DEBUG:matplotlib:CACHEDIR=/home/hayato/.cache/matplotlib
DEBUG:matplotlib.font_manager:Using fontManager instance from /home/hayato/.cache/matplotlib/fontlist-v330.json
DEBUG:matplotlib.pyplot:Loaded backend agg version unknown.
DEBUG:tensorflow:Falling back to TensorFlow client; we recommended you install the Cloud TPU client directly with pip install cloud-tpu-client.
DEBUG:h5py._conv:Creating converter from 7 to 5
DEBUG:h5py._conv:Creating converter from 5 to 7
DEBUG:h5py._conv:Creating converter from 7 to 5
DEBUG:h5py._conv:Creating converter from 5 to 7
DEBUG:easyprocess:version=0.3
DEBUG:pyvirtualdisplay:version=2.2
DEBUG:easyprocess:command: ['Xvfb', '-help']
DEBUG:easyprocess:process was started (pid=52384)
DEBUG:easyprocess:process has ended, return code=0
DEBUG:pyvirtualdisplay.abstractdisplay:command: ['Xvfb', '-br', '-nolisten', 'tcp', '-screen', '0', '1400x900x24', '-displayfd', '46']
DEBUG:pyvirtualdisplay.abstractdisplay:set $DISPLAY=:2


In [5]:
# helper functions
import functools

from acme import wrappers
import dm_env
import gym

def make_environment(level: str, evaluation: bool = False) -> dm_env.Environment:
  env = gym.make(level, full_action_space=True)

  max_episode_len = 108_000 if evaluation else 50_000

  return wrappers.wrap_all(env, [
      wrappers.GymAtariAdapter,
      functools.partial(
          wrappers.AtariWrapper,
          to_float=True,
          max_episode_len=max_episode_len,
          zero_discount_on_life_loss=True,
      ),
      wrappers.SinglePrecisionWrapper,
  ])

In [6]:
# Create a simple helper function to render a frame from the current state of
# the environment.
def render(env):
    return env.environment.render(mode='rgb_array')

def display_video(frames, filename='temp.mp4'):
  """Save and display video."""

  # Write video
  with imageio.get_writer(filename, fps=60) as video:
    for frame in frames:
      video.append_data(frame)

  # Read video and display the video
  video = open(filename, 'rb').read()
  b64_video = base64.b64encode(video)
  video_tag = ('<video  width="320" height="240" controls alt="test" '
               'src="data:video/mp4;base64,{0}">').format(b64_video.decode())

  return IPython.display.HTML(video_tag)

In [7]:
environment = make_environment('BreakoutDeterministic-v4')
environment_spec = acme.make_environment_spec(environment)
network = networks.DQNAtariNetwork(environment_spec.actions.num_values)

# Create a logger for the agent and environment loop.
# agent_logger = loggers.TerminalLogger(label='agent')
env_loop_logger = loggers.TerminalLogger(label='env_loop')

# agent = dqn.DQN(environment_spec, network, logger=agent_logger)
agent = dqn.DQN(environment_spec, network)

# Create an loop connecting this agent to the environment created above.
env_loop = acme.EnvironmentLoop(
    environment, agent, logger=env_loop_logger)
# env_loop = acme.EnvironmentLoop(environment, agent)

# Run a `num_episodes` training episodes.
# Rerun this cell until the agent has learned the given task.
# env_loop.run(num_episodes=1000)

INFO:absl:Attempting to restore checkpoint: None


In [17]:
# Run a `num_episodes` training episodes.
# Rerun this cell until the agent has learned the given task.
env_loop.run(num_episodes=5000)

INFO:root:[Learner] Loss = 0.366 | Steps = 753181 | Walltime = 100663.301
INFO:root:[Learner] Loss = 0.160 | Steps = 753188 | Walltime = 100664.305
INFO:root:[Learner] Loss = 0.354 | Steps = 753195 | Walltime = 100665.447
INFO:root:[Learner] Loss = 0.272 | Steps = 753203 | Walltime = 100666.526
INFO:root:[Env Loop] Episode Length = 212 | Episode Return = 21.0 | Episodes = 25001 | Steps = 6026648 | Steps Per Second = 54.055
INFO:root:[Learner] Loss = 0.202 | Steps = 753211 | Walltime = 100667.652
INFO:root:[Learner] Loss = 0.294 | Steps = 753218 | Walltime = 100668.690
INFO:root:[Env Loop] Episode Length = 103 | Episode Return = 8.0 | Episodes = 25002 | Steps = 6026751 | Steps Per Second = 56.444
INFO:root:[Learner] Loss = 0.248 | Steps = 753225 | Walltime = 100669.787
INFO:root:[Learner] Loss = 0.243 | Steps = 753232 | Walltime = 100670.790
INFO:root:[Learner] Loss = 0.219 | Steps = 753240 | Walltime = 100671.820
INFO:root:[Learner] Loss = 0.202 | Steps = 753248 | Walltime = 100672.827

INFO:root:[Learner] Loss = 0.302 | Steps = 753799 | Walltime = 100746.011
INFO:root:[Learner] Loss = 0.284 | Steps = 753807 | Walltime = 100747.029
INFO:root:[Learner] Loss = 0.382 | Steps = 753815 | Walltime = 100748.079
INFO:root:[Env Loop] Episode Length = 240 | Episode Return = 25.0 | Episodes = 25020 | Steps = 6031562 | Steps Per Second = 61.841
INFO:root:[Learner] Loss = 0.340 | Steps = 753823 | Walltime = 100749.105
INFO:root:[Learner] Loss = 0.258 | Steps = 753831 | Walltime = 100750.162
INFO:root:[Learner] Loss = 0.289 | Steps = 753839 | Walltime = 100751.188
INFO:root:[Learner] Loss = 0.221 | Steps = 753847 | Walltime = 100752.221
INFO:root:[Learner] Loss = 0.202 | Steps = 753855 | Walltime = 100753.270
INFO:root:[Learner] Loss = 0.367 | Steps = 753863 | Walltime = 100754.280
INFO:root:[Env Loop] Episode Length = 340 | Episode Return = 71.0 | Episodes = 25021 | Steps = 6031902 | Steps Per Second = 61.913
INFO:root:[Learner] Loss = 0.295 | Steps = 753871 | Walltime = 100755.32

INFO:root:[Learner] Loss = 0.323 | Steps = 754446 | Walltime = 100829.306
INFO:root:[Learner] Loss = 0.306 | Steps = 754454 | Walltime = 100830.346
INFO:root:[Env Loop] Episode Length = 363 | Episode Return = 76.0 | Episodes = 25038 | Steps = 6036638 | Steps Per Second = 60.365
INFO:root:[Learner] Loss = 0.445 | Steps = 754462 | Walltime = 100831.375
INFO:root:[Learner] Loss = 0.293 | Steps = 754470 | Walltime = 100832.384
INFO:root:[Learner] Loss = 0.258 | Steps = 754479 | Walltime = 100833.484
INFO:root:[Env Loop] Episode Length = 243 | Episode Return = 39.0 | Episodes = 25039 | Steps = 6036881 | Steps Per Second = 62.216
INFO:root:[Learner] Loss = 0.295 | Steps = 754487 | Walltime = 100834.574
INFO:root:[Learner] Loss = 0.196 | Steps = 754495 | Walltime = 100835.619
INFO:root:[Learner] Loss = 0.225 | Steps = 754503 | Walltime = 100836.681
INFO:root:[Learner] Loss = 0.296 | Steps = 754511 | Walltime = 100837.686
INFO:root:[Learner] Loss = 0.247 | Steps = 754520 | Walltime = 100838.77

INFO:root:[Learner] Loss = 0.299 | Steps = 755088 | Walltime = 100912.356
INFO:root:[Learner] Loss = 0.263 | Steps = 755096 | Walltime = 100913.365
INFO:root:[Env Loop] Episode Length = 317 | Episode Return = 48.0 | Episodes = 25056 | Steps = 6041774 | Steps Per Second = 61.583
INFO:root:[Learner] Loss = 0.299 | Steps = 755104 | Walltime = 100914.434
INFO:root:[Learner] Loss = 0.266 | Steps = 755112 | Walltime = 100915.440
INFO:root:[Learner] Loss = 0.216 | Steps = 755120 | Walltime = 100916.466
INFO:root:[Learner] Loss = 0.152 | Steps = 755128 | Walltime = 100917.526
INFO:root:[Learner] Loss = 0.211 | Steps = 755136 | Walltime = 100918.538
INFO:root:[Env Loop] Episode Length = 329 | Episode Return = 50.0 | Episodes = 25057 | Steps = 6042103 | Steps Per Second = 61.797
INFO:root:[Learner] Loss = 0.238 | Steps = 755144 | Walltime = 100919.632
INFO:root:[Learner] Loss = 0.290 | Steps = 755152 | Walltime = 100920.669
INFO:root:[Learner] Loss = 0.265 | Steps = 755160 | Walltime = 100921.69

INFO:root:[Learner] Loss = 0.186 | Steps = 755717 | Walltime = 100994.631
INFO:root:[Learner] Loss = 0.232 | Steps = 755725 | Walltime = 100995.678
INFO:root:[Env Loop] Episode Length = 323 | Episode Return = 49.0 | Episodes = 25075 | Steps = 6046810 | Steps Per Second = 62.440
INFO:root:[Learner] Loss = 0.256 | Steps = 755733 | Walltime = 100996.740
INFO:root:[Learner] Loss = 0.327 | Steps = 755741 | Walltime = 100997.788
INFO:root:[Env Loop] Episode Length = 157 | Episode Return = 13.0 | Episodes = 25076 | Steps = 6046967 | Steps Per Second = 62.568
INFO:root:[Learner] Loss = 0.254 | Steps = 755749 | Walltime = 100998.804
INFO:root:[Learner] Loss = 0.217 | Steps = 755757 | Walltime = 100999.907
INFO:root:[Learner] Loss = 0.240 | Steps = 755766 | Walltime = 101001.072
INFO:root:[Learner] Loss = 0.187 | Steps = 755774 | Walltime = 101002.152
INFO:root:[Learner] Loss = 0.366 | Steps = 755782 | Walltime = 101003.169
INFO:root:[Learner] Loss = 0.207 | Steps = 755790 | Walltime = 101004.17

...

INFO:root:[Learner] Loss = 0.295 | Steps = 922194 | Walltime = 122762.951
INFO:root:[Env Loop] Episode Length = 384 | Episode Return = 73.0 | Episodes = 29917 | Steps = 7378572 | Steps Per Second = 61.926
INFO:root:[Learner] Loss = 0.291 | Steps = 922202 | Walltime = 122764.007
INFO:root:[Learner] Loss = 0.328 | Steps = 922210 | Walltime = 122765.044
INFO:root:[Learner] Loss = 0.267 | Steps = 922218 | Walltime = 122766.090
INFO:root:[Env Loop] Episode Length = 210 | Episode Return = 27.0 | Episodes = 29918 | Steps = 7378782 | Steps Per Second = 61.982
INFO:root:[Learner] Loss = 0.263 | Steps = 922226 | Walltime = 122767.233
INFO:root:[Learner] Loss = 0.245 | Steps = 922234 | Walltime = 122768.332
INFO:root:[Learner] Loss = 0.357 | Steps = 922243 | Walltime = 122769.407
INFO:root:[Env Loop] Episode Length = 181 | Episode Return = 9.0 | Episodes = 29919 | Steps = 7378963 | Steps Per Second = 58.866
INFO:root:[Learner] Loss = 0.310 | Steps = 922251 | Walltime = 122770.496
INFO:root:[Learn

INFO:root:[Learner] Loss = 0.324 | Steps = 922822 | Walltime = 122845.373
INFO:root:[Env Loop] Episode Length = 249 | Episode Return = 28.0 | Episodes = 29936 | Steps = 7383586 | Steps Per Second = 61.021
INFO:root:[Learner] Loss = 0.253 | Steps = 922830 | Walltime = 122846.480
INFO:root:[Learner] Loss = 0.279 | Steps = 922838 | Walltime = 122847.517
INFO:root:[Learner] Loss = 0.198 | Steps = 922846 | Walltime = 122848.566
INFO:root:[Learner] Loss = 0.296 | Steps = 922854 | Walltime = 122849.621
INFO:root:[Learner] Loss = 0.233 | Steps = 922862 | Walltime = 122850.687
INFO:root:[Env Loop] Episode Length = 354 | Episode Return = 72.0 | Episodes = 29937 | Steps = 7383940 | Steps Per Second = 59.816
INFO:root:[Learner] Loss = 0.267 | Steps = 922869 | Walltime = 122851.694
INFO:root:[Learner] Loss = 0.173 | Steps = 922877 | Walltime = 122852.788
INFO:root:[Learner] Loss = 0.348 | Steps = 922885 | Walltime = 122853.847
INFO:root:[Learner] Loss = 0.282 | Steps = 922893 | Walltime = 122854.84

INFO:root:[Learner] Loss = 0.229 | Steps = 923461 | Walltime = 122928.879
INFO:root:[Env Loop] Episode Length = 354 | Episode Return = 72.0 | Episodes = 29953 | Steps = 7388687 | Steps Per Second = 61.514
INFO:root:[Learner] Loss = 0.245 | Steps = 923469 | Walltime = 122930.002
INFO:root:[Learner] Loss = 0.301 | Steps = 923477 | Walltime = 122931.113
INFO:root:[Learner] Loss = 0.264 | Steps = 923485 | Walltime = 122932.214
INFO:root:[Learner] Loss = 0.377 | Steps = 923493 | Walltime = 122933.353
INFO:root:[Env Loop] Episode Length = 251 | Episode Return = 29.0 | Episodes = 29954 | Steps = 7388938 | Steps Per Second = 57.007
INFO:root:[Learner] Loss = 0.272 | Steps = 923501 | Walltime = 122934.451
INFO:root:[Learner] Loss = 0.253 | Steps = 923509 | Walltime = 122935.579
INFO:root:[Learner] Loss = 0.250 | Steps = 923518 | Walltime = 122936.696
INFO:root:[Learner] Loss = 0.304 | Steps = 923526 | Walltime = 122937.710
INFO:root:[Env Loop] Episode Length = 276 | Episode Return = 35.0 | Epis

INFO:root:[Learner] Loss = 0.238 | Steps = 924099 | Walltime = 123012.775
INFO:root:[Learner] Loss = 0.275 | Steps = 924107 | Walltime = 123013.826
INFO:root:[Env Loop] Episode Length = 336 | Episode Return = 62.0 | Episodes = 29971 | Steps = 7393868 | Steps Per Second = 62.475
INFO:root:[Learner] Loss = 0.317 | Steps = 924115 | Walltime = 123014.905
INFO:root:[Learner] Loss = 0.270 | Steps = 924123 | Walltime = 123015.948
INFO:root:[Learner] Loss = 0.257 | Steps = 924131 | Walltime = 123017.043
INFO:root:[Env Loop] Episode Length = 233 | Episode Return = 27.0 | Episodes = 29972 | Steps = 7394101 | Steps Per Second = 60.508
INFO:root:[Learner] Loss = 0.215 | Steps = 924139 | Walltime = 123018.087
INFO:root:[Learner] Loss = 0.242 | Steps = 924147 | Walltime = 123019.130
INFO:root:[Learner] Loss = 0.309 | Steps = 924155 | Walltime = 123020.166
INFO:root:[Learner] Loss = 0.352 | Steps = 924163 | Walltime = 123021.216
INFO:root:[Learner] Loss = 0.237 | Steps = 924171 | Walltime = 123022.26

INFO:root:[Env Loop] Episode Length = 332 | Episode Return = 60.0 | Episodes = 29990 | Steps = 7398791 | Steps Per Second = 60.424
INFO:root:[Learner] Loss = 0.217 | Steps = 924728 | Walltime = 123095.273
INFO:root:[Learner] Loss = 0.234 | Steps = 924736 | Walltime = 123096.281
INFO:root:[Learner] Loss = 0.332 | Steps = 924744 | Walltime = 123097.342
INFO:root:[Env Loop] Episode Length = 180 | Episode Return = 22.0 | Episodes = 29991 | Steps = 7398971 | Steps Per Second = 61.370
INFO:root:[Learner] Loss = 0.251 | Steps = 924752 | Walltime = 123098.377
INFO:root:[Learner] Loss = 0.297 | Steps = 924760 | Walltime = 123099.481
INFO:root:[Learner] Loss = 0.226 | Steps = 924768 | Walltime = 123100.609
INFO:root:[Learner] Loss = 0.312 | Steps = 924776 | Walltime = 123101.652
INFO:root:[Learner] Loss = 0.301 | Steps = 924784 | Walltime = 123102.690
INFO:root:[Env Loop] Episode Length = 313 | Episode Return = 47.0 | Episodes = 29992 | Steps = 7399284 | Steps Per Second = 59.487
INFO:root:[Lear

In [18]:
timestep = environment.reset()
frames = [render(environment)]

while not timestep.last():
  # Simple environment loop.
  action = agent.select_action(timestep.observation)
  timestep = environment.step(action)

  # Render the scene and add it to the frame stack.
  frames.append(render(environment))

# Save and display a video of the behaviour.
display_video(np.array(frames))

In [19]:
env_loop.run(num_episodes=5000)

INFO:root:[Learner] Loss = 0.264 | Steps = 925089 | Walltime = 123145.352
INFO:root:[Learner] Loss = 0.312 | Steps = 925096 | Walltime = 123146.423
INFO:root:[Learner] Loss = 0.203 | Steps = 925103 | Walltime = 123147.471
INFO:root:[Learner] Loss = 0.344 | Steps = 925111 | Walltime = 123148.609
INFO:root:[Env Loop] Episode Length = 234 | Episode Return = 27.0 | Episodes = 30001 | Steps = 7401930 | Steps Per Second = 54.762
INFO:root:[Learner] Loss = 0.213 | Steps = 925118 | Walltime = 123149.618
INFO:root:[Learner] Loss = 0.251 | Steps = 925125 | Walltime = 123150.668
INFO:root:[Learner] Loss = 0.327 | Steps = 925132 | Walltime = 123151.699
INFO:root:[Learner] Loss = 0.241 | Steps = 925139 | Walltime = 123152.708
INFO:root:[Learner] Loss = 0.237 | Steps = 925147 | Walltime = 123153.781
INFO:root:[Learner] Loss = 0.191 | Steps = 925155 | Walltime = 123154.823
INFO:root:[Env Loop] Episode Length = 317 | Episode Return = 47.0 | Episodes = 30002 | Steps = 7402247 | Steps Per Second = 56.63

INFO:root:[Learner] Loss = 0.282 | Steps = 925689 | Walltime = 123228.318
INFO:root:[Learner] Loss = 0.303 | Steps = 925696 | Walltime = 123229.470
INFO:root:[Learner] Loss = 0.267 | Steps = 925703 | Walltime = 123230.480
INFO:root:[Learner] Loss = 0.270 | Steps = 925711 | Walltime = 123231.572
INFO:root:[Env Loop] Episode Length = 244 | Episode Return = 29.0 | Episodes = 30020 | Steps = 7406685 | Steps Per Second = 53.300
INFO:root:[Learner] Loss = 0.318 | Steps = 925718 | Walltime = 123232.699
INFO:root:[Learner] Loss = 0.302 | Steps = 925725 | Walltime = 123233.739
INFO:root:[Learner] Loss = 0.239 | Steps = 925733 | Walltime = 123234.810
INFO:root:[Learner] Loss = 0.317 | Steps = 925741 | Walltime = 123235.916
INFO:root:[Env Loop] Episode Length = 290 | Episode Return = 36.0 | Episodes = 30021 | Steps = 7406975 | Steps Per Second = 55.666
INFO:root:[Learner] Loss = 0.238 | Steps = 925748 | Walltime = 123236.951
INFO:root:[Learner] Loss = 0.213 | Steps = 925755 | Walltime = 123238.05

INFO:root:[Learner] Loss = 0.254 | Steps = 926323 | Walltime = 123312.445
INFO:root:[Learner] Loss = 0.289 | Steps = 926331 | Walltime = 123313.451
INFO:root:[Learner] Loss = 0.323 | Steps = 926339 | Walltime = 123314.463
INFO:root:[Learner] Loss = 0.247 | Steps = 926347 | Walltime = 123315.496
INFO:root:[Learner] Loss = 0.193 | Steps = 926355 | Walltime = 123316.553
INFO:root:[Learner] Loss = 0.292 | Steps = 926363 | Walltime = 123317.590
INFO:root:[Env Loop] Episode Length = 352 | Episode Return = 68.0 | Episodes = 30038 | Steps = 7411906 | Steps Per Second = 61.860
INFO:root:[Learner] Loss = 0.244 | Steps = 926371 | Walltime = 123318.670
INFO:root:[Learner] Loss = 0.225 | Steps = 926380 | Walltime = 123319.771
INFO:root:[Learner] Loss = 0.321 | Steps = 926389 | Walltime = 123320.881
INFO:root:[Learner] Loss = 0.225 | Steps = 926397 | Walltime = 123321.919
INFO:root:[Env Loop] Episode Length = 295 | Episode Return = 39.0 | Episodes = 30039 | Steps = 7412201 | Steps Per Second = 62.94

INFO:root:[Learner] Loss = 0.259 | Steps = 926948 | Walltime = 123394.925
INFO:root:[Learner] Loss = 0.274 | Steps = 926956 | Walltime = 123395.959
INFO:root:[Env Loop] Episode Length = 244 | Episode Return = 28.0 | Episodes = 30057 | Steps = 7416665 | Steps Per Second = 60.461
INFO:root:[Learner] Loss = 0.240 | Steps = 926964 | Walltime = 123396.969
INFO:root:[Learner] Loss = 0.272 | Steps = 926973 | Walltime = 123398.076
INFO:root:[Learner] Loss = 0.287 | Steps = 926982 | Walltime = 123399.196
INFO:root:[Learner] Loss = 0.234 | Steps = 926990 | Walltime = 123400.234
INFO:root:[Env Loop] Episode Length = 279 | Episode Return = 37.0 | Episodes = 30058 | Steps = 7416944 | Steps Per Second = 63.203
INFO:root:[Learner] Loss = 0.301 | Steps = 926998 | Walltime = 123401.336
INFO:root:[Learner] Loss = 0.241 | Steps = 927006 | Walltime = 123402.351
INFO:root:[Learner] Loss = 0.227 | Steps = 927014 | Walltime = 123403.370
INFO:root:[Env Loop] Episode Length = 176 | Episode Return = 15.0 | Epis

INFO:root:[Learner] Loss = 0.192 | Steps = 927574 | Walltime = 123477.647
INFO:root:[Learner] Loss = 0.254 | Steps = 927582 | Walltime = 123478.727
INFO:root:[Learner] Loss = 0.242 | Steps = 927590 | Walltime = 123479.773
INFO:root:[Env Loop] Episode Length = 210 | Episode Return = 27.0 | Episodes = 30076 | Steps = 7421765 | Steps Per Second = 61.390
INFO:root:[Learner] Loss = 0.251 | Steps = 927598 | Walltime = 123480.809
INFO:root:[Learner] Loss = 0.251 | Steps = 927606 | Walltime = 123481.849
INFO:root:[Learner] Loss = 0.223 | Steps = 927614 | Walltime = 123482.883
INFO:root:[Learner] Loss = 0.287 | Steps = 927623 | Walltime = 123484.009
INFO:root:[Learner] Loss = 0.290 | Steps = 927632 | Walltime = 123485.131
INFO:root:[Env Loop] Episode Length = 292 | Episode Return = 30.0 | Episodes = 30077 | Steps = 7422057 | Steps Per Second = 62.204
INFO:root:[Learner] Loss = 0.273 | Steps = 927640 | Walltime = 123486.224
INFO:root:[Learner] Loss = 0.246 | Steps = 927647 | Walltime = 123487.29

...

INFO:root:[Env Loop] Episode Length = 380 | Episode Return = 81.0 | Episodes = 34926 | Steps = 8795296 | Steps Per Second = 59.604
INFO:root:[Learner] Loss = 0.369 | Steps = 1099290 | Walltime = 146004.809
INFO:root:[Learner] Loss = 0.306 | Steps = 1099298 | Walltime = 146005.827
INFO:root:[Learner] Loss = 0.222 | Steps = 1099306 | Walltime = 146006.839
INFO:root:[Learner] Loss = 0.310 | Steps = 1099314 | Walltime = 146007.911
INFO:root:[Learner] Loss = 0.253 | Steps = 1099322 | Walltime = 146008.921
INFO:root:[Learner] Loss = 0.261 | Steps = 1099331 | Walltime = 146010.004
INFO:root:[Env Loop] Episode Length = 380 | Episode Return = 81.0 | Episodes = 34927 | Steps = 8795676 | Steps Per Second = 63.115
INFO:root:[Learner] Loss = 0.267 | Steps = 1099339 | Walltime = 146011.031
INFO:root:[Learner] Loss = 0.301 | Steps = 1099347 | Walltime = 146012.047
INFO:root:[Learner] Loss = 0.236 | Steps = 1099355 | Walltime = 146013.066
INFO:root:[Learner] Loss = 0.325 | Steps = 1099364 | Walltime =

INFO:root:[Learner] Loss = 0.255 | Steps = 1099920 | Walltime = 146086.963
INFO:root:[Learner] Loss = 0.267 | Steps = 1099929 | Walltime = 146088.064
INFO:root:[Env Loop] Episode Length = 299 | Episode Return = 37.0 | Episodes = 34944 | Steps = 8800444 | Steps Per Second = 63.582
INFO:root:[Learner] Loss = 0.182 | Steps = 1099937 | Walltime = 146089.069
INFO:root:[Learner] Loss = 0.228 | Steps = 1099945 | Walltime = 146090.100
INFO:root:[Learner] Loss = 0.174 | Steps = 1099953 | Walltime = 146091.115
INFO:root:[Learner] Loss = 0.294 | Steps = 1099961 | Walltime = 146092.124
INFO:root:[Learner] Loss = 0.258 | Steps = 1099969 | Walltime = 146093.148
INFO:root:[Env Loop] Episode Length = 369 | Episode Return = 76.0 | Episodes = 34945 | Steps = 8800813 | Steps Per Second = 63.228
INFO:root:[Learner] Loss = 0.333 | Steps = 1099978 | Walltime = 146094.310
INFO:root:[Learner] Loss = 0.214 | Steps = 1099986 | Walltime = 146095.339
INFO:root:[Learner] Loss = 0.289 | Steps = 1099994 | Walltime =

INFO:root:[Learner] Loss = 0.230 | Steps = 1100543 | Walltime = 146169.442
INFO:root:[Learner] Loss = 0.154 | Steps = 1100551 | Walltime = 146170.538
INFO:root:[Learner] Loss = 0.266 | Steps = 1100559 | Walltime = 146171.657
INFO:root:[Env Loop] Episode Length = 262 | Episode Return = 44.0 | Episodes = 34962 | Steps = 8805482 | Steps Per Second = 56.332
INFO:root:[Learner] Loss = 0.319 | Steps = 1100567 | Walltime = 146172.779
INFO:root:[Learner] Loss = 0.283 | Steps = 1100575 | Walltime = 146173.909
INFO:root:[Learner] Loss = 0.244 | Steps = 1100583 | Walltime = 146174.980
INFO:root:[Learner] Loss = 0.302 | Steps = 1100591 | Walltime = 146176.067
INFO:root:[Env Loop] Episode Length = 275 | Episode Return = 41.0 | Episodes = 34963 | Steps = 8805757 | Steps Per Second = 58.845
INFO:root:[Learner] Loss = 0.139 | Steps = 1100599 | Walltime = 146177.104
INFO:root:[Learner] Loss = 0.153 | Steps = 1100607 | Walltime = 146178.212
INFO:root:[Learner] Loss = 0.308 | Steps = 1100615 | Walltime =

INFO:root:[Learner] Loss = 0.303 | Steps = 1101172 | Walltime = 146252.539
INFO:root:[Learner] Loss = 0.292 | Steps = 1101180 | Walltime = 146253.618
INFO:root:[Env Loop] Episode Length = 248 | Episode Return = 28.0 | Episodes = 34980 | Steps = 8810482 | Steps Per Second = 58.902
INFO:root:[Learner] Loss = 0.288 | Steps = 1101187 | Walltime = 146254.624
INFO:root:[Learner] Loss = 0.206 | Steps = 1101195 | Walltime = 146255.657
INFO:root:[Learner] Loss = 0.275 | Steps = 1101203 | Walltime = 146256.729
INFO:root:[Learner] Loss = 0.297 | Steps = 1101211 | Walltime = 146257.788
INFO:root:[Env Loop] Episode Length = 198 | Episode Return = 21.0 | Episodes = 34981 | Steps = 8810680 | Steps Per Second = 60.140
INFO:root:[Learner] Loss = 0.192 | Steps = 1101219 | Walltime = 146258.819
INFO:root:[Learner] Loss = 0.317 | Steps = 1101227 | Walltime = 146259.857
INFO:root:[Learner] Loss = 0.224 | Steps = 1101235 | Walltime = 146260.922
INFO:root:[Env Loop] Episode Length = 253 | Episode Return = 34

INFO:root:[Learner] Loss = 0.283 | Steps = 1101799 | Walltime = 146335.849
INFO:root:[Learner] Loss = 0.277 | Steps = 1101807 | Walltime = 146336.876
INFO:root:[Env Loop] Episode Length = 348 | Episode Return = 77.0 | Episodes = 34998 | Steps = 8815456 | Steps Per Second = 59.659
INFO:root:[Learner] Loss = 0.336 | Steps = 1101814 | Walltime = 146337.887
INFO:root:[Learner] Loss = 0.269 | Steps = 1101822 | Walltime = 146338.996
INFO:root:[Learner] Loss = 0.333 | Steps = 1101830 | Walltime = 146340.091
INFO:root:[Learner] Loss = 0.184 | Steps = 1101838 | Walltime = 146341.115
INFO:root:[Env Loop] Episode Length = 295 | Episode Return = 47.0 | Episodes = 34999 | Steps = 8815751 | Steps Per Second = 59.834
INFO:root:[Learner] Loss = 0.246 | Steps = 1101846 | Walltime = 146342.142
INFO:root:[Learner] Loss = 0.276 | Steps = 1101854 | Walltime = 146343.150
INFO:root:[Learner] Loss = 0.339 | Steps = 1101862 | Walltime = 146344.184
INFO:root:[Learner] Loss = 0.307 | Steps = 1101870 | Walltime =

In [20]:
env_loop.run(num_episodes=5000)

INFO:root:[Learner] Loss = 0.255 | Steps = 1101885 | Walltime = 146347.247
INFO:root:[Learner] Loss = 0.333 | Steps = 1101893 | Walltime = 146348.303
INFO:root:[Learner] Loss = 0.332 | Steps = 1101902 | Walltime = 146349.416
INFO:root:[Learner] Loss = 0.205 | Steps = 1101911 | Walltime = 146350.523
INFO:root:[Env Loop] Episode Length = 275 | Episode Return = 42.0 | Episodes = 35001 | Steps = 8816328 | Steps Per Second = 61.874
INFO:root:[Learner] Loss = 0.268 | Steps = 1101919 | Walltime = 146351.606
INFO:root:[Learner] Loss = 0.301 | Steps = 1101927 | Walltime = 146352.672
INFO:root:[Learner] Loss = 0.266 | Steps = 1101935 | Walltime = 146353.705
INFO:root:[Env Loop] Episode Length = 173 | Episode Return = 16.0 | Episodes = 35002 | Steps = 8816501 | Steps Per Second = 60.770
INFO:root:[Learner] Loss = 0.261 | Steps = 1101943 | Walltime = 146354.780
INFO:root:[Learner] Loss = 0.285 | Steps = 1101951 | Walltime = 146355.843
INFO:root:[Learner] Loss = 0.278 | Steps = 1101959 | Walltime =

INFO:root:[Learner] Loss = 0.321 | Steps = 1102481 | Walltime = 146427.096
INFO:root:[Learner] Loss = 0.277 | Steps = 1102489 | Walltime = 146428.137
INFO:root:[Learner] Loss = 0.260 | Steps = 1102497 | Walltime = 146429.186
INFO:root:[Learner] Loss = 0.221 | Steps = 1102505 | Walltime = 146430.272
INFO:root:[Env Loop] Episode Length = 214 | Episode Return = 19.0 | Episodes = 35021 | Steps = 8821046 | Steps Per Second = 60.050
INFO:root:[Learner] Loss = 0.247 | Steps = 1102513 | Walltime = 146431.395
INFO:root:[Learner] Loss = 0.245 | Steps = 1102521 | Walltime = 146432.429
INFO:root:[Learner] Loss = 0.292 | Steps = 1102530 | Walltime = 146433.549
INFO:root:[Learner] Loss = 0.274 | Steps = 1102539 | Walltime = 146434.658
INFO:root:[Env Loop] Episode Length = 275 | Episode Return = 34.0 | Episodes = 35022 | Steps = 8821321 | Steps Per Second = 62.040
INFO:root:[Learner] Loss = 0.203 | Steps = 1102547 | Walltime = 146435.713
INFO:root:[Learner] Loss = 0.215 | Steps = 1102555 | Walltime =

INFO:root:[Learner] Loss = 0.393 | Steps = 1103103 | Walltime = 146507.905
INFO:root:[Learner] Loss = 0.228 | Steps = 1103112 | Walltime = 146509.020
INFO:root:[Env Loop] Episode Length = 357 | Episode Return = 67.0 | Episodes = 35040 | Steps = 8825935 | Steps Per Second = 63.053
INFO:root:[Learner] Loss = 0.248 | Steps = 1103120 | Walltime = 146510.076
INFO:root:[Learner] Loss = 0.287 | Steps = 1103128 | Walltime = 146511.091
INFO:root:[Learner] Loss = 0.283 | Steps = 1103136 | Walltime = 146512.101
INFO:root:[Env Loop] Episode Length = 187 | Episode Return = 21.0 | Episodes = 35041 | Steps = 8826122 | Steps Per Second = 62.167
INFO:root:[Learner] Loss = 0.325 | Steps = 1103144 | Walltime = 146513.171
INFO:root:[Learner] Loss = 0.281 | Steps = 1103153 | Walltime = 146514.294
INFO:root:[Learner] Loss = 0.266 | Steps = 1103161 | Walltime = 146515.319
INFO:root:[Env Loop] Episode Length = 210 | Episode Return = 27.0 | Episodes = 35042 | Steps = 8826332 | Steps Per Second = 62.725
INFO:ro

INFO:root:[Env Loop] Episode Length = 170 | Episode Return = 26.0 | Episodes = 35059 | Steps = 8830696 | Steps Per Second = 60.535
INFO:root:[Learner] Loss = 0.207 | Steps = 1103717 | Walltime = 146589.805
INFO:root:[Learner] Loss = 0.265 | Steps = 1103725 | Walltime = 146590.843
INFO:root:[Env Loop] Episode Length = 154 | Episode Return = 14.0 | Episodes = 35060 | Steps = 8830850 | Steps Per Second = 59.633
INFO:root:[Learner] Loss = 0.283 | Steps = 1103733 | Walltime = 146591.937
INFO:root:[Learner] Loss = 0.178 | Steps = 1103741 | Walltime = 146592.974
INFO:root:[Learner] Loss = 0.357 | Steps = 1103749 | Walltime = 146594.037
INFO:root:[Learner] Loss = 0.299 | Steps = 1103757 | Walltime = 146595.167
INFO:root:[Env Loop] Episode Length = 243 | Episode Return = 28.0 | Episodes = 35061 | Steps = 8831093 | Steps Per Second = 60.263
INFO:root:[Learner] Loss = 0.221 | Steps = 1103765 | Walltime = 146596.190
INFO:root:[Learner] Loss = 0.259 | Steps = 1103774 | Walltime = 146597.303
INFO:ro

INFO:root:[Learner] Loss = 0.289 | Steps = 1104346 | Walltime = 146672.004
INFO:root:[Env Loop] Episode Length = 172 | Episode Return = 22.0 | Episodes = 35077 | Steps = 8835796 | Steps Per Second = 61.629
INFO:root:[Learner] Loss = 0.297 | Steps = 1104354 | Walltime = 146673.053
INFO:root:[Learner] Loss = 0.368 | Steps = 1104362 | Walltime = 146674.056
INFO:root:[Learner] Loss = 0.304 | Steps = 1104370 | Walltime = 146675.116
INFO:root:[Learner] Loss = 0.306 | Steps = 1104378 | Walltime = 146676.130
INFO:root:[Learner] Loss = 0.336 | Steps = 1104386 | Walltime = 146677.158
INFO:root:[Env Loop] Episode Length = 312 | Episode Return = 55.0 | Episodes = 35078 | Steps = 8836108 | Steps Per Second = 62.288
INFO:root:[Learner] Loss = 0.232 | Steps = 1104394 | Walltime = 146678.179
INFO:root:[Learner] Loss = 0.222 | Steps = 1104402 | Walltime = 146679.201
INFO:root:[Learner] Loss = 0.321 | Steps = 1104410 | Walltime = 146680.247
INFO:root:[Learner] Loss = 0.330 | Steps = 1104419 | Walltime =

...

INFO:root:[Learner] Loss = 0.335 | Steps = 1276401 | Walltime = 169316.580
INFO:root:[Learner] Loss = 0.214 | Steps = 1276409 | Walltime = 169317.697
INFO:root:[Learner] Loss = 0.242 | Steps = 1276417 | Walltime = 169318.794
INFO:root:[Learner] Loss = 0.298 | Steps = 1276425 | Walltime = 169319.864
INFO:root:[Env Loop] Episode Length = 337 | Episode Return = 47.0 | Episodes = 39927 | Steps = 10212439 | Steps Per Second = 59.691
INFO:root:[Learner] Loss = 0.240 | Steps = 1276433 | Walltime = 169320.938
INFO:root:[Learner] Loss = 0.318 | Steps = 1276441 | Walltime = 169322.016
INFO:root:[Learner] Loss = 0.322 | Steps = 1276449 | Walltime = 169323.110
INFO:root:[Learner] Loss = 0.337 | Steps = 1276457 | Walltime = 169324.215
INFO:root:[Env Loop] Episode Length = 259 | Episode Return = 40.0 | Episodes = 39928 | Steps = 10212698 | Steps Per Second = 57.996
INFO:root:[Learner] Loss = 0.137 | Steps = 1276464 | Walltime = 169325.223
INFO:root:[Learner] Loss = 0.225 | Steps = 1276472 | Walltime

INFO:root:[Learner] Loss = 0.319 | Steps = 1277020 | Walltime = 169399.633
INFO:root:[Learner] Loss = 0.251 | Steps = 1277028 | Walltime = 169400.672
INFO:root:[Learner] Loss = 0.322 | Steps = 1277036 | Walltime = 169401.700
INFO:root:[Learner] Loss = 0.143 | Steps = 1277044 | Walltime = 169402.707
INFO:root:[Env Loop] Episode Length = 241 | Episode Return = 28.0 | Episodes = 39945 | Steps = 10217383 | Steps Per Second = 62.150
INFO:root:[Learner] Loss = 0.331 | Steps = 1277052 | Walltime = 169403.762
INFO:root:[Learner] Loss = 0.261 | Steps = 1277060 | Walltime = 169404.810
INFO:root:[Learner] Loss = 0.263 | Steps = 1277068 | Walltime = 169405.888
INFO:root:[Learner] Loss = 0.274 | Steps = 1277076 | Walltime = 169406.947
INFO:root:[Learner] Loss = 0.253 | Steps = 1277084 | Walltime = 169407.958
INFO:root:[Learner] Loss = 0.176 | Steps = 1277093 | Walltime = 169409.065
INFO:root:[Env Loop] Episode Length = 362 | Episode Return = 75.0 | Episodes = 39946 | Steps = 10217745 | Steps Per Se

INFO:root:[Learner] Loss = 0.326 | Steps = 1277633 | Walltime = 169481.676
INFO:root:[Learner] Loss = 0.249 | Steps = 1277641 | Walltime = 169482.718
INFO:root:[Learner] Loss = 0.268 | Steps = 1277649 | Walltime = 169483.737
INFO:root:[Learner] Loss = 0.173 | Steps = 1277657 | Walltime = 169484.785
INFO:root:[Env Loop] Episode Length = 254 | Episode Return = 32.0 | Episodes = 39964 | Steps = 10222291 | Steps Per Second = 61.163
INFO:root:[Learner] Loss = 0.287 | Steps = 1277665 | Walltime = 169485.840
INFO:root:[Learner] Loss = 0.218 | Steps = 1277673 | Walltime = 169486.894
INFO:root:[Learner] Loss = 0.229 | Steps = 1277681 | Walltime = 169487.942
INFO:root:[Learner] Loss = 0.265 | Steps = 1277689 | Walltime = 169488.981
INFO:root:[Learner] Loss = 0.250 | Steps = 1277697 | Walltime = 169490.021
INFO:root:[Env Loop] Episode Length = 289 | Episode Return = 37.0 | Episodes = 39965 | Steps = 10222580 | Steps Per Second = 60.756
INFO:root:[Learner] Loss = 0.218 | Steps = 1277705 | Walltime

INFO:root:[Learner] Loss = 0.298 | Steps = 1278260 | Walltime = 169564.129
INFO:root:[Env Loop] Episode Length = 155 | Episode Return = 14.0 | Episodes = 39982 | Steps = 10227124 | Steps Per Second = 60.416
INFO:root:[Learner] Loss = 0.198 | Steps = 1278268 | Walltime = 169565.163
INFO:root:[Learner] Loss = 0.266 | Steps = 1278276 | Walltime = 169566.225
INFO:root:[Learner] Loss = 0.321 | Steps = 1278283 | Walltime = 169567.289
INFO:root:[Learner] Loss = 0.231 | Steps = 1278291 | Walltime = 169568.453
INFO:root:[Env Loop] Episode Length = 247 | Episode Return = 33.0 | Episodes = 39983 | Steps = 10227371 | Steps Per Second = 57.333
INFO:root:[Learner] Loss = 0.292 | Steps = 1278299 | Walltime = 169569.500
INFO:root:[Learner] Loss = 0.261 | Steps = 1278307 | Walltime = 169570.571
INFO:root:[Learner] Loss = 0.367 | Steps = 1278316 | Walltime = 169571.706
INFO:root:[Learner] Loss = 0.211 | Steps = 1278324 | Walltime = 169572.755
INFO:root:[Learner] Loss = 0.226 | Steps = 1278332 | Walltime

INFO:root:[Learner] Loss = 0.206 | Steps = 1278888 | Walltime = 169646.932
INFO:root:[Learner] Loss = 0.284 | Steps = 1278896 | Walltime = 169648.021
INFO:root:[Env Loop] Episode Length = 263 | Episode Return = 30.0 | Episodes = 40000 | Steps = 10232191 | Steps Per Second = 60.668


In [ ]:
env_loop.run(num_episodes=5000)

INFO:root:[Learner] Loss = 0.286 | Steps = 1278904 | Walltime = 169649.134
INFO:root:[Learner] Loss = 0.279 | Steps = 1278912 | Walltime = 169650.185
INFO:root:[Learner] Loss = 0.230 | Steps = 1278920 | Walltime = 169651.205
INFO:root:[Env Loop] Episode Length = 182 | Episode Return = 19.0 | Episodes = 40001 | Steps = 10232373 | Steps Per Second = 60.087
INFO:root:[Learner] Loss = 0.209 | Steps = 1278927 | Walltime = 169652.223
INFO:root:[Learner] Loss = 0.271 | Steps = 1278935 | Walltime = 169653.286
INFO:root:[Learner] Loss = 0.287 | Steps = 1278943 | Walltime = 169654.345
INFO:root:[Env Loop] Episode Length = 224 | Episode Return = 24.0 | Episodes = 40002 | Steps = 10232597 | Steps Per Second = 59.293
INFO:root:[Learner] Loss = 0.376 | Steps = 1278951 | Walltime = 169655.456
INFO:root:[Learner] Loss = 0.348 | Steps = 1278960 | Walltime = 169656.587
INFO:root:[Learner] Loss = 0.372 | Steps = 1278968 | Walltime = 169657.621
INFO:root:[Learner] Loss = 0.288 | Steps = 1278976 | Walltime

INFO:root:[Learner] Loss = 0.175 | Steps = 1279524 | Walltime = 169731.286
INFO:root:[Learner] Loss = 0.242 | Steps = 1279532 | Walltime = 169732.344
INFO:root:[Learner] Loss = 0.199 | Steps = 1279541 | Walltime = 169733.466
INFO:root:[Env Loop] Episode Length = 249 | Episode Return = 37.0 | Episodes = 40018 | Steps = 10237329 | Steps Per Second = 62.362
INFO:root:[Learner] Loss = 0.220 | Steps = 1279549 | Walltime = 169734.555
INFO:root:[Learner] Loss = 0.315 | Steps = 1279557 | Walltime = 169735.589
INFO:root:[Learner] Loss = 0.250 | Steps = 1279565 | Walltime = 169736.614
INFO:root:[Env Loop] Episode Length = 216 | Episode Return = 22.0 | Episodes = 40019 | Steps = 10237545 | Steps Per Second = 60.586
INFO:root:[Learner] Loss = 0.266 | Steps = 1279573 | Walltime = 169737.727
INFO:root:[Learner] Loss = 0.171 | Steps = 1279581 | Walltime = 169738.778
INFO:root:[Env Loop] Episode Length = 147 | Episode Return = 12.0 | Episodes = 40020 | Steps = 10237692 | Steps Per Second = 60.894
INFO

INFO:root:[Learner] Loss = 0.270 | Steps = 1280131 | Walltime = 169810.412
INFO:root:[Learner] Loss = 0.256 | Steps = 1280140 | Walltime = 169811.506
INFO:root:[Env Loop] Episode Length = 267 | Episode Return = 36.0 | Episodes = 40038 | Steps = 10242148 | Steps Per Second = 64.181
INFO:root:[Learner] Loss = 0.263 | Steps = 1280148 | Walltime = 169812.538
INFO:root:[Learner] Loss = 0.286 | Steps = 1280156 | Walltime = 169813.547
INFO:root:[Learner] Loss = 0.256 | Steps = 1280164 | Walltime = 169814.588
INFO:root:[Learner] Loss = 0.249 | Steps = 1280172 | Walltime = 169815.643
INFO:root:[Learner] Loss = 0.314 | Steps = 1280180 | Walltime = 169816.678
INFO:root:[Env Loop] Episode Length = 329 | Episode Return = 47.0 | Episodes = 40039 | Steps = 10242477 | Steps Per Second = 62.101
INFO:root:[Learner] Loss = 0.177 | Steps = 1280188 | Walltime = 169817.725
INFO:root:[Learner] Loss = 0.232 | Steps = 1280196 | Walltime = 169818.754
INFO:root:[Learner] Loss = 0.206 | Steps = 1280204 | Walltime

INFO:root:[Env Loop] Episode Length = 328 | Episode Return = 46.0 | Episodes = 40054 | Steps = 10247300 | Steps Per Second = 60.217
INFO:root:[Learner] Loss = 0.288 | Steps = 1280796 | Walltime = 169896.495
INFO:root:[Learner] Loss = 0.156 | Steps = 1280804 | Walltime = 169897.534
INFO:root:[Learner] Loss = 0.358 | Steps = 1280812 | Walltime = 169898.551
INFO:root:[Learner] Loss = 0.217 | Steps = 1280820 | Walltime = 169899.625
INFO:root:[Learner] Loss = 0.270 | Steps = 1280829 | Walltime = 169900.735
INFO:root:[Env Loop] Episode Length = 375 | Episode Return = 58.0 | Episodes = 40055 | Steps = 10247675 | Steps Per Second = 61.973
INFO:root:[Learner] Loss = 0.257 | Steps = 1280837 | Walltime = 169901.767
INFO:root:[Learner] Loss = 0.189 | Steps = 1280845 | Walltime = 169902.811
INFO:root:[Learner] Loss = 0.169 | Steps = 1280853 | Walltime = 169903.832
INFO:root:[Learner] Loss = 0.243 | Steps = 1280861 | Walltime = 169904.835
INFO:root:[Learner] Loss = 0.205 | Steps = 1280869 | Walltime

INFO:root:[Learner] Loss = 0.284 | Steps = 1281460 | Walltime = 169983.142
INFO:root:[Learner] Loss = 0.197 | Steps = 1281468 | Walltime = 169984.171
INFO:root:[Learner] Loss = 0.223 | Steps = 1281476 | Walltime = 169985.180
INFO:root:[Learner] Loss = 0.237 | Steps = 1281484 | Walltime = 169986.190
INFO:root:[Learner] Loss = 0.336 | Steps = 1281492 | Walltime = 169987.257
INFO:root:[Learner] Loss = 0.219 | Steps = 1281500 | Walltime = 169988.299
INFO:root:[Env Loop] Episode Length = 531 | Episode Return = 54.0 | Episodes = 40070 | Steps = 10253010 | Steps Per Second = 61.845
INFO:root:[Learner] Loss = 0.271 | Steps = 1281508 | Walltime = 169989.301
INFO:root:[Learner] Loss = 0.207 | Steps = 1281516 | Walltime = 169990.317
INFO:root:[Learner] Loss = 0.275 | Steps = 1281524 | Walltime = 169991.319
INFO:root:[Learner] Loss = 0.222 | Steps = 1281532 | Walltime = 169992.321
INFO:root:[Learner] Loss = 0.278 | Steps = 1281540 | Walltime = 169993.333
INFO:root:[Learner] Loss = 0.276 | Steps = 

...

INFO:root:[Learner] Loss = 0.300 | Steps = 1330958 | Walltime = 176505.501
INFO:root:[Learner] Loss = 0.190 | Steps = 1330966 | Walltime = 176506.503
INFO:root:[Env Loop] Episode Length = 359 | Episode Return = 55.0 | Episodes = 41497 | Steps = 10648777 | Steps Per Second = 63.131
INFO:root:[Learner] Loss = 0.203 | Steps = 1330974 | Walltime = 176507.557
INFO:root:[Learner] Loss = 0.290 | Steps = 1330982 | Walltime = 176508.580
INFO:root:[Learner] Loss = 0.247 | Steps = 1330990 | Walltime = 176509.613
INFO:root:[Env Loop] Episode Length = 195 | Episode Return = 26.0 | Episodes = 41498 | Steps = 10648972 | Steps Per Second = 61.515
INFO:root:[Learner] Loss = 0.220 | Steps = 1330998 | Walltime = 176510.710
INFO:root:[Learner] Loss = 0.248 | Steps = 1331006 | Walltime = 176511.764
INFO:root:[Learner] Loss = 0.254 | Steps = 1331014 | Walltime = 176512.787
INFO:root:[Learner] Loss = 0.233 | Steps = 1331022 | Walltime = 176513.813
INFO:root:[Learner] Loss = 0.305 | Steps = 1331030 | Walltime

INFO:root:[Learner] Loss = 0.266 | Steps = 1331561 | Walltime = 176584.569
INFO:root:[Learner] Loss = 0.198 | Steps = 1331569 | Walltime = 176585.620
INFO:root:[Learner] Loss = 0.252 | Steps = 1331577 | Walltime = 176586.654
INFO:root:[Env Loop] Episode Length = 154 | Episode Return = 14.0 | Episodes = 41517 | Steps = 10653631 | Steps Per Second = 61.063
INFO:root:[Learner] Loss = 0.151 | Steps = 1331585 | Walltime = 176587.668
INFO:root:[Learner] Loss = 0.254 | Steps = 1331593 | Walltime = 176588.753
INFO:root:[Learner] Loss = 0.247 | Steps = 1331601 | Walltime = 176589.817
INFO:root:[Env Loop] Episode Length = 213 | Episode Return = 24.0 | Episodes = 41518 | Steps = 10653844 | Steps Per Second = 59.506
INFO:root:[Learner] Loss = 0.327 | Steps = 1331608 | Walltime = 176590.829
INFO:root:[Learner] Loss = 0.286 | Steps = 1331616 | Walltime = 176591.913
INFO:root:[Learner] Loss = 0.225 | Steps = 1331624 | Walltime = 176593.006
INFO:root:[Learner] Loss = 0.267 | Steps = 1331632 | Walltime

INFO:root:[Learner] Loss = 0.165 | Steps = 1332171 | Walltime = 176665.120
INFO:root:[Learner] Loss = 0.216 | Steps = 1332179 | Walltime = 176666.160
INFO:root:[Learner] Loss = 0.224 | Steps = 1332187 | Walltime = 176667.202
INFO:root:[Env Loop] Episode Length = 195 | Episode Return = 25.0 | Episodes = 41536 | Steps = 10658495 | Steps Per Second = 61.690
INFO:root:[Learner] Loss = 0.281 | Steps = 1332195 | Walltime = 176668.283
INFO:root:[Learner] Loss = 0.220 | Steps = 1332203 | Walltime = 176669.347
INFO:root:[Learner] Loss = 0.267 | Steps = 1332211 | Walltime = 176670.452
INFO:root:[Env Loop] Episode Length = 235 | Episode Return = 32.0 | Episodes = 41537 | Steps = 10658730 | Steps Per Second = 57.549
INFO:root:[Learner] Loss = 0.257 | Steps = 1332218 | Walltime = 176671.532
INFO:root:[Learner] Loss = 0.183 | Steps = 1332226 | Walltime = 176672.540
INFO:root:[Learner] Loss = 0.303 | Steps = 1332233 | Walltime = 176673.554
INFO:root:[Learner] Loss = 0.160 | Steps = 1332241 | Walltime

INFO:root:[Env Loop] Episode Length = 409 | Episode Return = 20.0 | Episodes = 41551 | Steps = 10663295 | Steps Per Second = 52.504
INFO:root:[Learner] Loss = 0.289 | Steps = 1332792 | Walltime = 176754.556
INFO:root:[Learner] Loss = 0.246 | Steps = 1332800 | Walltime = 176755.587
INFO:root:[Learner] Loss = 0.205 | Steps = 1332808 | Walltime = 176756.694
INFO:root:[Learner] Loss = 0.283 | Steps = 1332815 | Walltime = 176757.729
INFO:root:[Learner] Loss = 0.315 | Steps = 1332823 | Walltime = 176758.843
INFO:root:[Learner] Loss = 0.179 | Steps = 1332830 | Walltime = 176759.897
INFO:root:[Learner] Loss = 0.251 | Steps = 1332836 | Walltime = 176760.917
INFO:root:[Learner] Loss = 0.218 | Steps = 1332844 | Walltime = 176762.031
INFO:root:[Learner] Loss = 0.284 | Steps = 1332852 | Walltime = 176763.112
INFO:root:[Env Loop] Episode Length = 538 | Episode Return = 35.0 | Episodes = 41552 | Steps = 10663833 | Steps Per Second = 55.696
INFO:root:[Learner] Loss = 0.229 | Steps = 1332859 | Walltime

INFO:root:[Learner] Loss = 0.238 | Steps = 1333410 | Walltime = 176845.456
INFO:root:[Learner] Loss = 0.268 | Steps = 1333416 | Walltime = 176846.591
INFO:root:[Learner] Loss = 0.175 | Steps = 1333423 | Walltime = 176847.704
INFO:root:[Env Loop] Episode Length = 142 | Episode Return = 13.0 | Episodes = 41566 | Steps = 10668386 | Steps Per Second = 47.159
INFO:root:[Learner] Loss = 0.236 | Steps = 1333429 | Walltime = 176848.765
INFO:root:[Learner] Loss = 0.298 | Steps = 1333435 | Walltime = 176849.908
INFO:root:[Learner] Loss = 0.270 | Steps = 1333440 | Walltime = 176850.969
INFO:root:[Learner] Loss = 0.244 | Steps = 1333446 | Walltime = 176852.136
INFO:root:[Learner] Loss = 0.360 | Steps = 1333451 | Walltime = 176853.205
INFO:root:[Learner] Loss = 0.375 | Steps = 1333456 | Walltime = 176854.234
INFO:root:[Learner] Loss = 0.239 | Steps = 1333461 | Walltime = 176855.344
INFO:root:[Learner] Loss = 0.213 | Steps = 1333467 | Walltime = 176856.459
INFO:root:[Env Loop] Episode Length = 345 |

In [ ]:
agent

In [ ]:
from tensorflow.saved_model import load

In [ ]:
agent = load('/home/hayato/acme/b8ca9590-d77d-11eb-b169-332db766104b/checkpoints/dqn_learner')

In [ ]:
# agent.save('pong_model')
from acme.tf.savers import Checkpointer, Snapshotter

In [ ]:
checkpointer = Checkpointer(objects_to_save={'model': network})

In [ ]:
checkpointer._checkpoint_dir = '/home/hayato/acme/b8ca9590-d77d-11eb-b169-332db766104b/checkpoints/dqn_learner'

In [ ]:
agent._checkpointer

In [ ]:
from tensorflow.train import Checkpoint

In [ ]:
checkpointer._checkpoint_manager._latest_checkpoint = '/home/hayato/acme/b8ca9590-d77d-11eb-b169-332db766104b/checkpoints/dqn_learner'

In [ ]:
# checkpointer = Checkpointer(objects_to_save={'model': agent})
snapshot = Snapshotter(objects_to_save={"model": network})

In [ ]:
snapshot.save()